## Code from last lecture

In [ ]:
def loadFasta(filename):
    """ Parses a classically formatted and possibly 
        compressed FASTA file into a list of headers 
        and fragment sequences for each sequence contained"""
    if (filename.endswith(".gz")):
        fp = gzip.open(filename, 'r')
    else:
        fp = open(filename, 'r')
    # split at headers
    data = fp.read().split('>')
    fp.close()
    # ignore whatever appears before the 1st header
    data.pop(0)     
    headers = []
    sequences = []
    for sequence in data:
        lines = sequence.split('\n')
        headers.append(lines.pop(0))
        # add an extra "+" to make string "1-referenced"
        sequences.append('+' + ''.join(lines))
    return (headers, sequences)

In [ ]:
header, seq = loadFasta("data/GCA_000001405.15_GRCh38_genomic.fna")
print(len(header), "sequences")
for i in range(len(header)):
    if header[i].startswith("CM") or header[i].startswith("J0"):
        print(header[i])
        print(len(seq[i])-1, "bases", seq[i][:30], "...", seq[i][-30:])

## A function to construct the reverse-complement version of a DNA sequence

In [5]:
def revComp(dnaSeq):
    return ''.join([{'A':'T','C':'G','G':'C','T':'A'}[base] for base in reversed(dnaSeq)])

In [6]:
print(revComp("GAGACAT"))
print(revComp("ATGTCTC"))

ATGTCTC
GAGACAT


## Output eacch chromosome as a simple string to speed up future processing

In [ ]:
header, seq = loadFasta("data/GCA_000001405.15_GRCh38_genomic.fna")
print(len(header), "sequences")
for i in range(len(header)):
    if header[i].startswith("CM") or header[i].startswith("J0"):
        start = header[i].find('chromosome ')
        chromo = header[i][start+11:header[i].find(',')] if (start >= 0) else "MT"
        with open("data/Chr%s.seq" % chromo, 'w') as fp:
            fp.write(seq[i])            

## Find the frequency of all k-mers in the genome

# Warning: This next cell takes a while...

In [ ]:
import time

chromo = [str(i) for i in xrange(1,23)] + ['X', 'Y', 'MT']

kmerCount = {}
K = 11
L = 0
for contig in chromo:
    tick = time.time()
    with open("Chr%s.seq" % contig, 'r') as fp:
        seq = fp.read()
    for i in xrange(1,len(seq)-K+1):
        kmer = seq[i:i+K]
        for base in "RYSWKMBDHVN":
            if (base in kmer):
                break
        else:
            kmerCount[kmer] = kmerCount.get(kmer,0) + 1
            kmer = revComp(kmer)
            kmerCount[kmer] = kmerCount.get(kmer,0) + 1
    tock = time.time()
    print(contig, len(seq)-1, len(kmerCount), "%6.2f secs" % (tock - tick))
    tick = tock
    L += len(seq) - 1
print(L, len(kmerCount))

## Plot the kmer distribution

In [ ]:
import matplotlib
import matplotlib.pyplot as plot
%matplotlib inline

# Compute a histogram of kmer-counts (i.e. how many kmers appear 1 time, 2 times, 3 times ...)
maxcount = 500
hist = [0 for i in range(maxcount)]
for kmer in kmerCount:
    count = kmerCount[kmer]
    if (count < maxcount):
        hist[count] += 1

fig = plot.figure(figsize=(10,6))
plot.plot([i for i in range(maxcount)], hist)
plot.show()